In [1]:
import os
import pandas as pd
import numpy as np
from sqlalchemy import create_engine,text
from scipy import stats
import plotly.express as px
import toml
import psrc_theme
import geopandas as gpd
import plotly.express as px
import plotly.graph_objects as go

%matplotlib inline
from IPython.display import display, HTML

# to show plotly figures in quarto HTML file
import plotly.io as pio
pio.renderers.default = "plotly_mimetype+notebook_connected"
pio.templates.default = "simple_white+psrc_color" # set plotly template

input_config = toml.load(os.path.join(os.getcwd(), '..\\..\\..\\..\\configuration', 'input_configuration.toml'))
valid_config = toml.load(os.path.join(os.getcwd(), '..\\..\\..\\..\\configuration', 'validation_configuration.toml'))
summary_config = toml.load(os.path.join(os.getcwd(), '..\\..\\..\\..\\configuration', 'summary_configuration.toml'))

# create connection
conn = create_engine('sqlite:///../../../../inputs/db/'+input_config['db_name'])
# summary data location
csv_path = os.path.join(valid_config['model_dir'], 'outputs/validation')

# table format
pd.options.display.float_format = '{:0,.0f}'.format
format_percent = "{:,.2%}".format

## transit boarding

### boarding by mode

In [2]:
# Process 2024 observed data
df_obs = pd.read_sql(text("SELECT * FROM observed_transit_boardings"), con=conn.connect())

df_obs["route_id"] = df_obs["route_id"].astype("int")

df_obs = df_obs[df_obs['year'].isin([2023,2024])]

df_obs = pd.pivot_table(df_obs, index='route_id', values='observed_daily', columns='year', aggfunc='sum')
df_obs = df_obs.reset_index()



In [3]:

# Load model results and calculate modeled daily boarding by line
df_transit_line = pd.read_csv(os.path.join(valid_config['model_dir'], 'outputs/transit/transit_line_results.csv'))
df_model = df_transit_line.copy()
df_model_daily = (
    df_model.groupby(["route_code", "mode",'agency_code'])
    .agg({"description": "first", "boardings": "sum"})
    .reset_index()
)

# Merge modeled with observed boarding data
df_model_daily["route_code"] = df_model_daily["route_code"].astype("int")
df = df_model_daily.merge(
    df_obs, left_on="route_code", right_on="route_id", how="left"
)

df.rename(
    columns={
        "boardings": "Model",
        2023: "2023 Spring Observed",
        2024: "2024 Spring Observed",
    },
    inplace=True,
)


df['agency'] = df['agency_code'].astype('int').astype('str').map(summary_config['agency_lookup'])
df_line_boardings_23_24 = df.copy()

In [4]:
df = pd.read_csv(os.path.join(csv_path, 'daily_boardings_by_mode.csv')).sort_values('model_boardings', ascending=False)
table_df = df.copy()
table_df['mode_name'] = table_df['mode'].map({'c':'Commuter Rail','b':'Bus','r':'Rail','f':'Ferry (1)','p':'Ferry (2)'})
# table_df[['mode','mode_name','model_boardings','2023','2024']]
table_df.rename(
    columns={
        "model_boardings": "Model",
        "2023": "2023 Spring Observed",
        "2024": "2024 Spring Observed",
    },
    inplace=True,
)
table_df[['mode','mode_name','Model','2023 Spring Observed','2024 Spring Observed']]

mode      mode_name     Model  2023 Spring Observed  2024 Spring Observed
0    b            Bus 1,043,004                     0                     0
4    r           Rail   473,300                     0                     0
2    f      Ferry (1)    29,981                     0                     0
3    p      Ferry (2)    14,401                    83                    95
1    c  Commuter Rail     8,362                     0                     0

In [5]:
df_boarding_line = pd.read_csv(os.path.join(csv_path,'daily_boardings_by_line.csv'), index_col='description')
# df_boarding_line[['2023','model_boardings']] = df_boarding_line[['2023','model_boardings']].astype('float')

df = df_boarding_line[df_boarding_line['route_code'].isin([6996,6999,6998])].reset_index()
df.index = df['route_code']
df.loc[6996,'line'] = 'Link 1 Line'
df.loc[6999,'line'] = 'Sounder'
df.loc[6998,'line'] = 'Sounder'
df = df.groupby('line').sum()[['model_boardings','2023','2024']]
df.rename(columns={'model_boardings': 'Model'}, inplace=True)


df['2023 % diff'] = (df['Model'].astype(float)-df['2023'].astype(float))/df['2023'].astype(float)
df['2024 % diff'] = (df['Model'].astype(float)-df['2024'].astype(float))/df['2024'].astype(float)
df[['2023 % diff']] = df[['2023 % diff']].applymap(format_percent)
df[['2024 % diff']] = df[['2024 % diff']].applymap(format_percent)

for col in ['Model','2023','2024']:
    df[col] = df[col].astype(float).map('{:,.0f}'.format)
df

C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\2196298059.py:15: FutureWarning:

DataFrame.applymap has been deprecated. Use DataFrame.map instead.

C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\2196298059.py:16: FutureWarning:

DataFrame.applymap has been deprecated. Use DataFrame.map instead.



Model 2023 2024 2023 % diff 2024 % diff
line                                               
Link 1 Line     0    0    0        nan%        nan%
Sounder         0    0    0        nan%        nan%

### boarding by agency

In [6]:
df = pd.read_csv(os.path.join(csv_path, 'daily_boardings_by_agency.csv'))
# # plot_df = df.melt(id_vars=['agency'], value_vars=['observed_boardings', 'model_boardings'],
# #                   var_name='source', value_name='count')
# df_boarding_line = pd.read_csv(os.path.join(csv_path,'daily_boardings_by_line.csv'), index_col='description')
# df = df_boarding_line.groupby('agency').sum()[['model_boardings','2023','2024']].sort_values('2023', ascending=False)
df.rename(columns={'model_boardings': 'Model'}, inplace=True)
for col in ['Model','2023','2024']:
    df[col] = df[col].astype(float).map('{:,.0f}'.format)
df

agency Model   2023   2024
0  Washington Ferries   260  7,883  8,614

In [7]:
# df = pd.read_csv(os.path.join(csv_path, 'daily_boardings_by_line.csv')).sort_values('observed_boardings', ascending=False)
df = df_line_boardings_23_24.copy()
df
df = df[df['mode'].isin(['b'])]
df = df.groupby(['agency'])[['Model','2023 Spring Observed','2024 Spring Observed']].sum()
df


Model  2023 Spring Observed  2024 Spring Observed
agency                                                               
Community Transit 108,692                     0                     0
Everett Transit    21,712                     0                     0
King County Metro 781,895                     0                     0
Kitsap Transit     21,230                     0                     0
Pierce Transit     75,469                     0                     0
Sound Transit      34,006                     0                     0

### boarding by key route

In [8]:

df = df_line_boardings_23_24[df_line_boardings_23_24['mode'].isin(['f','p'])][['route_code','description','agency','Model','2023 Spring Observed','2024 Spring Observed']]
df = df[df['route_code'].isin([4200,4201,4203,4204,5001,5002,5003,5004,5005,5006,5007,1973,1975])].reset_index()
df.drop(['route_code','agency'], axis=1, inplace=True)
df_table = df.copy()
# df_table[['perc_diff']] = df_table[['perc_diff']].applymap(format_percent)
df_table.sort_values('Model', ascending=False)

index           description  Model  2023 Spring Observed  \
0     14  WSF Southworth - Vas    260                    83   

   2024 Spring Observed  
0                    95

In [9]:
# if len(df) > 0:
#     ax = df.plot(kind='scatter', x='observed_boardings', y='model_boardings')
#     lim = df[['observed_boardings','model_boardings']].max().max()*1.05
#     ax.set_ylim(0,lim)
#     ax.set_xlim(0,lim)
#     x = np.linspace(*ax.get_xlim())
#     ax.plot(x, x)
#     slope, intercept, r_value, p_value, std_err = stats.linregress(df['observed_boardings'],df['model_boardings'])
#     print('r^2 ' + str('') + ': ' + str(r_value))

In [10]:
df = df_line_boardings_23_24[df_line_boardings_23_24['route_code'].isin([6996,6999,6998])].reset_index()
df['description'] = df['route_code'].map({6998: 'Sounder South', 6999: 'Sounder North',6996: 'Link Red Line'})
# df.drop(['route_code','agency'], axis=1, inplace=True)
df_table = df[['route_code','description','agency','Model','2023 Spring Observed','2024 Spring Observed']].copy()
# df_table[['perc_diff']] = df_table[['perc_diff']].applymap(format_percent)
df_table

Empty DataFrame
Columns: [route_code, description, agency, Model, 2023 Spring Observed, 2024 Spring Observed]
Index: []

In [11]:
# if len(df) > 0:
#     ax = df.plot(kind='scatter', x='observed_boardings', y='model_boardings')
#     lim = df[['observed_boardings','model_boardings']].max().max()*1.05
#     ax.set_ylim(0,lim)
#     ax.set_xlim(0,lim)
#     x = np.linspace(*ax.get_xlim())
#     ax.plot(x, x)
#     slope, intercept, r_value, p_value, std_err = stats.linregress(df['observed_boardings'],df['model_boardings'])
#     print('r^2 ' + str('') + ': ' + str(r_value))

In [12]:
# df = df_boarding_key[df_boarding_key['route_code'].isin([1671,1672,1673,1674,1675,1676,6550,1007,1040,1997,1998])].reset_index()
# df['description'] = df['route_code'].map({1671: 'A Line RapidRide', 1672: 'B Line RapidRide',
#                                             1673: 'C Line RapidRide', 1674: 'D Line RapidRide',
#                                             1675: 'E Line RapidRide', 1676: 'F Line RapidRide',
#                                             6550: 'Sound Transit 550', 1040: 'KC Metro 40', 1007: 'KC Metro 7',
#                                             1997: 'SLU Streetcar', 1998: 'First Hill Streetcar'})
# df.drop(['route_code','agency'], axis=1, inplace=True)

df = df_line_boardings_23_24[df_line_boardings_23_24['route_code'].isin([1671,1672,1673,1674,1675,1676,6550,1007,1040,1997,1998])].reset_index()
df['description'] = df['route_code'].map({1671: 'A Line RapidRide', 1672: 'B Line RapidRide',
                                            1673: 'C Line RapidRide', 1674: 'D Line RapidRide',
                                            1675: 'E Line RapidRide', 1676: 'F Line RapidRide',
                                            6550: 'Sound Transit 550', 1040: 'KC Metro 40', 1007: 'KC Metro 7',
                                            1997: 'SLU Streetcar', 1998: 'First Hill Streetcar'})
# df.drop(['route_code','agency'], axis=1, inplace=True)
df_table = df[['route_code','description','agency','Model','2023 Spring Observed','2024 Spring Observed']].copy()

df_table = df[['route_code','description','agency','Model','2023 Spring Observed','2024 Spring Observed']].copy()
df_table.sort_values('Model', ascending=False)

Empty DataFrame
Columns: [route_code, description, agency, Model, 2023 Spring Observed, 2024 Spring Observed]
Index: []

In [13]:
# if len(df) > 0:
#     ax = df.plot(kind='scatter', x='observed_boardings', y='model_boardings')
#     lim = df[['observed_boardings', 'model_boardings']].max().max() * 1.05
#     ax.set_ylim(0, lim)
#     ax.set_xlim(0, lim)
#     x = np.linspace(*ax.get_xlim())
#     ax.plot(x, x)
#     slope, intercept, r_value, p_value, std_err = stats.linregress(df['observed_boardings'], df['model_boardings'])
#     print('r^2 ' + str('') + ': ' + str(r_value))

### Top routes by agency

In [14]:
# df = pd.read_csv(os.path.join(csv_path, 'daily_boardings_by_line.csv'))
df = df_line_boardings_23_24.copy()
# df_top = pd.DataFrame()
# for agency in df['agency'].unique():
#     _df = df[df['agency'] == agency].sort_values('model_boardings', ascending=False).head(8)
#     df_top = pd.concat([df_top, _df])
# df = df_top[['agency','description','mode','model_boardings','observed_boardings','diff','perc_diff']]
cols=['agency','description','mode','Model','2023 Spring Observed','2024 Spring Observed']

In [15]:
agency = 'King County Metro'
df[df['agency'] == agency].sort_values('Model', ascending=False).head(10)[cols]

agency           description mode   Model  \
0   King County Metro          RR (E Line)N    b 781,895   
7   King County Metro  Vashon to Downtown S    f  10,114   
10  King County Metro  West Seattle to Down    p   3,682   

    2023 Spring Observed  2024 Spring Observed  
0                    NaN                   NaN  
7                    NaN                   NaN  
10                   NaN                   NaN

In [16]:
agency = 'Sound Transit'
df[df['agency'] == agency].sort_values('Model', ascending=False).head(10)[cols]

agency           description mode   Model  2023 Spring Observed  \
13  Sound Transit               1 LineN    r 473,300                   NaN   
4   Sound Transit  OWL Everett - Seattl    b  34,006                   NaN   
6   Sound Transit               N LineS    c   8,362                   NaN   

    2024 Spring Observed  
13                   NaN  
4                    NaN  
6                    NaN

In [17]:
agency = 'Community Transit'
df[df['agency'] == agency].sort_values('Model', ascending=False).head(10)[cols]

agency description mode   Model  2023 Spring Observed  \
2  Community Transit     CT1102N    b 108,692                   NaN   

   2024 Spring Observed  
2                   NaN

In [18]:
agency = 'Pierce Transit'
df[df['agency'] == agency].sort_values('Model', ascending=False).head(10)[cols]

agency           description mode  Model  2023 Spring Observed  \
1  Pierce Transit  Purdy Gig Harbor Tac    b 75,469                   NaN   

   2024 Spring Observed  
1                   NaN

In [19]:
agency = 'Kitsap Transit'
df[df['agency'] == agency].sort_values('Model', ascending=False).head(10)[cols]

agency           description mode  Model  2023 Spring Observed  \
3   Kitsap Transit         Fletcher BayE    b 21,230                   NaN   
8   Kitsap Transit           Fast FerryN    f  7,028                   NaN   
11  Kitsap Transit  Annapolis to Bremert    p  6,199                   NaN   

    2024 Spring Observed  
3                    NaN  
8                    NaN  
11                   NaN

In [20]:
agency = 'Everett Transit'
df[df['agency'] == agency].sort_values('Model', ascending=False).head(10)[cols]

agency        description mode  Model  2023 Spring Observed  \
5  Everett Transit  Casino ConnectorE    b 21,712                   NaN   

   2024 Spring Observed  
5                   NaN

### boarding by time of day

In [21]:
def create_tod_chart(df):
    # Create a figure
    fig = go.Figure()

    descriptions = df['description'].unique()

    # Add traces for each description
    for description in descriptions:
        _df = df[df['description'] == description].copy()
        _df = pd.pivot_table(_df, index='tod', columns='description', values='boardings')

        tod_list = []
        for tod in ['5to6', '6to7', '7to8', '8to9', '9to10', '14to15', '15to16', '16to17', '17to18']:
            if tod in _df.index:
                tod_list.append(tod)

        # Smooth out time periods
        if '10to14' in _df.index:
            _df.loc['10to11'] = _df.loc['10to14'] / 4.0
            _df.loc['11to12'] = _df.loc['10to14'] / 4.0
            _df.loc['12to13'] = _df.loc['10to14'] / 4.0
            _df.loc['13to14'] = _df.loc['10to14'] / 4.0
            tod_list += ['10to11', '11to12', '12to13', '13to14']
            _df.drop('10to14', inplace=True)

        if '18to20' in _df.index:
            _df.loc['18to19'] = _df.loc['18to20'] / 2.0
            _df.loc['19to20'] = _df.loc['18to20'] / 2.0
            tod_list += ['18to19', '19to20']
            _df.drop('18to20', inplace=True)
        if '20to5' in _df.index:
            tod_list += ['20to21', '21to22', '22to23', '23to0', '0to1', '1to2', '2to3', '3to4', '4to5']
            _df.loc['20to21'] = _df.loc['20to5'] / 9.0
            _df.loc['21to22'] = _df.loc['20to5'] / 9.0
            _df.loc['22to23'] = _df.loc['20to5'] / 9.0
            _df.loc['23to0'] = _df.loc['20to5'] / 9.0
            _df.loc['0to1'] = _df.loc['20to5'] / 9.0
            _df.loc['1to2'] = _df.loc['20to5'] / 9.0
            _df.loc['2to3'] = _df.loc['20to5'] / 9.0
            _df.loc['3to4'] = _df.loc['20to5'] / 9.0
            _df.loc['4to5'] = _df.loc['20to5'] / 9.0
            _df.drop('20to5', inplace=True)

        _df = _df.reset_index()
        _df.index = _df.tod
        _df.drop('tod', axis=1, inplace=True)
        _df = _df.loc[_df.index, description]
        _df = _df.loc[tod_list]

        fig.add_trace(go.Scatter(x=_df.index, y=_df, mode='lines', name=description, visible=False))

    # Make the first trace visible
    fig.data[0].visible = True

    # Create dropdown menu
    dropdown_buttons = [
        {'label': description, 'method': 'update', 'args': [{'visible': [description == desc for desc in descriptions]}, {'title': f'Route: {description} (Daily Boardings: {df[df["description"] == description]["boardings"].sum():,.0f})'}]}
        for description in descriptions
    ]

    # Update layout with dropdown
    fig.update_layout(
        updatemenus=[{
            'buttons': dropdown_buttons,
            'direction': 'down',
            'showactive': True,
        }],
        title=f'Route: {descriptions[0]} (Daily Boardings: {df[df["description"] == descriptions[0]]["boardings"].sum():,.0f})',
        height=500,
        width=900,
        font=dict(size=11),
        yaxis_tickformat='.00f'
    )

    return fig

In [22]:
df_transit_line['agency'] = df_transit_line['agency_code'].astype('int').astype('str').map(summary_config['agency_lookup'])

agency = 'King County Metro'
df = df_transit_line[df_transit_line['agency'] == agency]
df = df.groupby(['tod', 'description']).agg({'boardings': 'sum'}).reset_index()
fig = create_tod_chart(df)
fig.show()

In [23]:
agency = 'Sound Transit'
df = df_transit_line[df_transit_line['agency'] == agency]
df = df.groupby(['tod', 'description']).agg({'boardings': 'sum'}).reset_index()
fig = create_tod_chart(df)
fig.show()

In [24]:
agency = 'Community Transit'
df = df_transit_line[df_transit_line['agency'] == agency]
df = df.groupby(['tod', 'description']).agg({'boardings': 'sum'}).reset_index()
fig = create_tod_chart(df)
fig.show()

In [25]:
agency = 'Pierce Transit'
df = df_transit_line[df_transit_line['agency'] == agency]
df = df.groupby(['tod', 'description']).agg({'boardings': 'sum'}).reset_index()
fig = create_tod_chart(df)
fig.show()

In [26]:
agency = 'Kitsap Transit'
df = df_transit_line[df_transit_line['agency'] == agency]
df = df.groupby(['tod', 'description']).agg({'boardings': 'sum'}).reset_index()
fig = create_tod_chart(df)
fig.show()

In [27]:
agency = 'Everett Transit'
df = df_transit_line[df_transit_line['agency'] == agency]
df = df.groupby(['tod', 'description']).agg({'boardings': 'sum'}).reset_index()
fig = create_tod_chart(df)
fig.show()

### boarding on lines by agency

In [28]:
df = pd.read_csv(os.path.join(csv_path,'daily_boardings_by_line.csv'), index_col='agency')

In [29]:
#| layout-ncol: 2
df = pd.read_csv(os.path.join(csv_path,'daily_boardings_by_line.csv'), index_col='agency')
# df = df[-df['agency_id'].isnull()]
df = df[~df['route_id'].isnull()]
for agency in np.unique(df.index):
    _df = df.loc[agency,:]
    if (type(_df) == pd.core.frame.DataFrame) & (len(df) > 0):
        ax = _df.plot(kind='scatter', x='2023', y='model_boardings', label=agency)
        lim = _df[['2023','model_boardings']].max().max()*1.05
        ax.set_ylim(0,lim)
        ax.set_xlim(0,lim)
        x = np.linspace(*ax.get_xlim())
        ax.plot(x, x)
        slope, intercept, r_value, p_value, std_err = stats.linregress(_df['2023'],_df['model_boardings'])
        print('r^2 ' + str(agency) + ': ' + str(r_value))

### boarding by light rail station

In [30]:
df = pd.read_csv(os.path.join(csv_path,'light_rail_boardings.csv'), index_col='station_name')
df['diff'] = df['model_boardings']-df['observed_boardings']
df['percent_diff'] = df['diff']/df['observed_boardings']

df_table = df.copy()
df_table[['percent_diff']] = df_table[['percent_diff']].applymap(format_percent)
df_table

line_1_station_list = ['Northgate Station','Roosevelt Station','University District Station', 
                'Husky Stadium', 'Capitol Hill', 'Westlake', 'Symphony', 'Pioneer Square',
                "Int'l District",  'Stadium', 'SODO', 'Beacon Hill',
               'Mount Baker', 'Columbia City', 'Othello', 'Rainier Beach',
                "Tukwila Int'l Blvd", 'SeaTac/Airport', 'Angle Lake']
t_line_station_list = ['Tacoma Dome Station', 'S 25th St Station', 'Union Station',
       'Convention Center Station', 'Commerce Station']

C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\2244156880.py:6: FutureWarning:

DataFrame.applymap has been deprecated. Use DataFrame.map instead.



In [31]:
line_1_df = df_table.loc[line_1_station_list]
df_totals = line_1_df.copy()
df_totals.loc['total']= df_totals.sum(numeric_only=True)
df_totals

observed_boardings  model_boardings    diff  \
station_name                                                               
Northgate Station                        10,384            9,372  -1,012   
Roosevelt Station                         4,349           11,237   6,888   
University District Station               7,563           20,125  12,562   
Husky Stadium                             6,134           11,762   5,628   
Capitol Hill                              7,667           15,526   7,859   
Westlake                                  8,845           31,295  22,450   
Symphony                                  4,324           17,176  12,852   
Pioneer Square                            2,400           17,645  15,245   
Int'l District                            4,399           27,338  22,939   
Stadium                                   1,731            2,582     851   
SODO                                      1,669           13,016  11,347   
Beacon Hill                               2,147            3,030     883   
Mount Baker                               1,861            3,441   1,580   
Columbia City                             1,630            2,176     546   
Othello                                   2,030            1,545    -485   
Rainier Beach                             1,495            4,208   2,713   
Tukwila Int'l Blvd                        2,298            5,256   2,958   
SeaTac/Airport                            4,731           15,117  10,386   
Angle Lake                                3,865            4,449     584   
total                                    79,522          216,297 136,775   

                            percent_diff  
station_name                              
Northgate Station                 -9.75%  
Roosevelt Station                158.39%  
University District Station      166.10%  
Husky Stadium                     91.75%  
Capitol Hill                     102.51%  
Westlake                         253.82%  
Symphony                         297.22%  
Pioneer Square                   635.22%  
Int'l District                   521.47%  
Stadium                           49.17%  
SODO                             679.89%  
Beacon Hill                       41.11%  
Mount Baker                       84.88%  
Columbia City                     33.48%  
Othello                          -23.91%  
Rainier Beach                    181.49%  
Tukwila Int'l Blvd               128.74%  
SeaTac/Airport                   219.53%  
Angle Lake                        15.11%  
total                                NaN

In [32]:
fig = px.line(line_1_df[['observed_boardings','model_boardings']])
fig.update_layout(height=500, width=900, font=dict(size=11),
                  yaxis_tickformat = '.00f')
fig.show()

In [33]:
t_line_df = df_table.loc[t_line_station_list]
t_line_df.loc['total']= t_line_df.sum(numeric_only=True)
t_line_df

observed_boardings  model_boardings   diff  \
station_name                                                            
Tacoma Dome Station                       494           10,546 10,052   
S 25th St Station                         120              614    494   
Union Station                             420              284   -136   
Convention Center Station                  91              187     96   
Commerce Station                          294              422    128   
total                                   1,419           12,054 10,635   

                          percent_diff  
station_name                            
Tacoma Dome Station          2,034.75%  
S 25th St Station              411.97%  
Union Station                  -32.33%  
Convention Center Station      105.79%  
Commerce Station                43.70%  
total                              NaN

In [34]:
df_combined = df.copy()

df_combined['station_group'] = df.index
df_combined.loc[['Westlake'],'station_group'] = 'Westlake/Symphony'
df_combined.loc[['Symphony'],'station_group'] = 'Westlake/Symphony'

df_combined.loc[['Pioneer Square'],'station_group'] = "Pioneer Square/Int'l District"
df_combined.loc[["Int'l District"],'station_group'] = "Pioneer Square/Int'l District"

df_combined.loc[['Stadium'],'station_group'] = 'Stadium/SODO'
df_combined.loc[['SODO'],'station_group'] = 'Stadium/SODO'

df_combined.loc[['Beacon Hill'],'station_group'] = 'Beacon Hill/Mount Baker'
df_combined.loc[['Mount Baker'],'station_group'] = 'Beacon Hill/Mount Baker'

df_combined.loc[['Othello'],'station_group'] = 'Othello/Rainier Beach'
df_combined.loc[['Rainier Beach'],'station_group'] = 'Othello/Rainier Beach'

df_combined.loc[['University District Station'],'station_group'] = 'U District/Husky Stadium'
df_combined.loc[['Husky Stadium'],'station_group'] = 'U District/Husky Stadium'

df_combined.loc[['Northgate Station'],'station_group'] = 'Northgate/Roosevelt'
df_combined.loc[['Roosevelt Station'],'station_group'] = 'Northgate/Roosevelt'

df_combined = df_combined.groupby('station_group').sum()[['observed_boardings','model_boardings']]
df_combined['diff'] = df_combined['model_boardings']-df_combined['observed_boardings']
df_combined['percent_diff'] = df_combined['diff']/df_combined['observed_boardings']
df_combined[['percent_diff']] = df_combined[['percent_diff']].applymap(format_percent)

df_combined = df_combined.loc[['Northgate/Roosevelt','U District/Husky Stadium','Capitol Hill','Westlake/Symphony',"Pioneer Square/Int'l District",
                             'Stadium/SODO','Beacon Hill/Mount Baker','Columbia City','Othello/Rainier Beach',
                             "Tukwila Int'l Blvd",'SeaTac/Airport','Angle Lake']]
df_combined

C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\4163746875.py:28: FutureWarning:

DataFrame.applymap has been deprecated. Use DataFrame.map instead.



observed_boardings  model_boardings   diff  \
station_group                                                               
Northgate/Roosevelt                        14,733           20,609  5,876   
U District/Husky Stadium                   13,697           31,887 18,190   
Capitol Hill                                7,667           15,526  7,859   
Westlake/Symphony                          13,169           48,471 35,302   
Pioneer Square/Int'l District               6,799           44,984 38,185   
Stadium/SODO                                3,400           15,598 12,198   
Beacon Hill/Mount Baker                     4,008            6,470  2,462   
Columbia City                               1,630            2,176    546   
Othello/Rainier Beach                       3,525            5,753  2,228   
Tukwila Int'l Blvd                          2,298            5,256  2,958   
SeaTac/Airport                              4,731           15,117 10,386   
Angle Lake                                  3,865            4,449    584   

                              percent_diff  
station_group                               
Northgate/Roosevelt                 39.89%  
U District/Husky Stadium           132.80%  
Capitol Hill                       102.51%  
Westlake/Symphony                  268.07%  
Pioneer Square/Int'l District      561.62%  
Stadium/SODO                       358.78%  
Beacon Hill/Mount Baker             61.44%  
Columbia City                       33.48%  
Othello/Rainier Beach               63.20%  
Tukwila Int'l Blvd                 128.74%  
SeaTac/Airport                     219.53%  
Angle Lake                          15.11%

In [35]:

fig = px.line(df_combined[['observed_boardings','model_boardings']])
fig.update_layout(height=500, width=900, font=dict(size=11),
                  yaxis_tickformat = '.00f')
fig.show()

In [36]:
df_obs = pd.read_sql(
    "SELECT * FROM light_rail_station_boardings WHERE year IN (2023, 2024)",
    con=conn,
)
df_obs.rename(columns={"boardings": "observed_boardings"}, inplace=True)

# df_obs.groupby(['year','station_name']).sum()
df_obs = pd.pivot_table(df_obs, values='observed_boardings', columns='year', index='station_name', aggfunc=np.sum)
df_obs = df_obs.fillna(0)
df_obs

df = pd.read_csv(os.path.join(csv_path,'light_rail_boardings.csv'), index_col='station_name', usecols=['station_name','model_boardings'])
df = df.merge(df_obs,  left_index=True, right_index=True, how='outer')
df = df[df.index != 'Total']
df = df[~df['model_boardings'].isnull()]
df = df.loc[line_1_station_list]

C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\3655372430.py:8: FutureWarning:

The provided callable <function sum at 0x000001E03D5E9260> is currently using DataFrameGroupBy.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "sum" instead.



In [37]:
fig = px.line(df[[2023,2024,'model_boardings']])
fig.update_layout(height=500, width=900, font=dict(size=11),
                  yaxis_tickformat = '.00f')
fig.show()

## light rail stop transfers

In [38]:
df = pd.read_csv(os.path.join(csv_path,'light_rail_transfers.csv'), index_col='station_name')
df[['percent_diff']] = df[['percent_diff']].applymap(format_percent)
df.loc[line_1_station_list]

C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\2177680554.py:2: FutureWarning:

DataFrame.applymap has been deprecated. Use DataFrame.map instead.



modeled_transfer_rate  observed_transfer_rate  \
station_name                                                                 
Northgate Station                                0                     -99   
Roosevelt Station                                0                     -99   
University District Station                      0                     -99   
Husky Stadium                                    1                     -99   
Capitol Hill                                     0                     -99   
Westlake                                         0                       0   
Symphony                                         0                       0   
Pioneer Square                                   0                       0   
Int'l District                                   1                       0   
Stadium                                          0                       0   
SODO                                             1                       0   
Beacon Hill                                      0                       0   
Mount Baker                                      0                       0   
Columbia City                                    0                       0   
Othello                                          0                       0   
Rainier Beach                                    1                       0   
Tukwila Int'l Blvd                               1                       0   
SeaTac/Airport                                   0                       0   
Angle Lake                                       0                     -99   

                             diff percent_diff  
station_name                                    
Northgate Station              99     -100.32%  
Roosevelt Station              99     -100.29%  
University District Station    99     -100.13%  
Husky Stadium                 100     -100.97%  
Capitol Hill                   99     -100.22%  
Westlake                       -0      -78.92%  
Symphony                       -0      -66.18%  
Pioneer Square                  0      104.35%  
Int'l District                  0       67.25%  
Stadium                         0      192.06%  
SODO                            0       73.42%  
Beacon Hill                     0       32.65%  
Mount Baker                    -0       -6.81%  
Columbia City                  -0      -94.10%  
Othello                        -0      -47.56%  
Rainier Beach                   0      112.14%  
Tukwila Int'l Blvd              0      141.95%  
SeaTac/Airport                 -0      -54.38%  
Angle Lake                     99     -100.35%

## Park and Ride

In [39]:
df_trip = pd.read_csv(os.path.join(valid_config['model_dir'], 'outputs/daysim/_trip.tsv'), sep='\t')
pnr_boardings = df_trip[(df_trip['otaz'].isin(range(3750,4001))) & (df_trip['mode']==6)]
pnr_boardings = pnr_boardings.groupby('otaz').count()[['trexpfac']].reset_index()

In [40]:
stations = [
    {"id": 3751, "name": "Tukwila Station (CR)"},
    {"id": 3752, "name": "Tacoma Dome Station"},
    {"id": 3753, "name": "South Tacoma (CR)"},
    {"id": 3754, "name": "Everett Station (CR)"},
    {"id": 3755, "name": "Sumner Station (CR)"},
    {"id": 3756, "name": "Mukilteo Station"},
    {"id": 3757, "name": "Kent Station (CR)"},
    {"id": 3758, "name": "Auburn Station (CR)"},
    {"id": 3759, "name": "Lakewood (CR)"},
    {"id": 3760, "name": "Gateway P&R"},
    {"id": 3761, "name": "Puyallup Station (SB)"},
    {"id": 3762, "name": "Twin Lakes P&R"},
    {"id": 3763, "name": "Crossroads Neighborhood Church"},
    {"id": 3764, "name": "Overlake Transit Center"},
    {"id": 3765, "name": "Redondo Heights P&R"},
    {"id": 3766, "name": "North Gig Harbor/Kimball Drive"},
    {"id": 3767, "name": "Duvall P&R"},
    {"id": 3768, "name": "Roy 'Y' P&R"},
    {"id": 3769, "name": "South Hill (Elim Evangelical)"},
    {"id": 3770, "name": "Parkland Transit Center"},
    {"id": 3771, "name": "SR-512/I-5 (Lakewood)"},
    {"id": 3772, "name": "Center Street P&R"},
    {"id": 3773, "name": "Tacoma Mall Transit Center"},
    {"id": 3774, "name": "South Tacoma West"},
    {"id": 3775, "name": "South Tacoma East - 2"},
    {"id": 3776, "name": "Narrows P&R"},
    {"id": 3777, "name": "North Purdy/Purdy Crescent"},
    {"id": 3778, "name": "Point Defiance Ferry"},
    {"id": 3779, "name": "South Federal P&R"},
    {"id": 3780, "name": "Sultan P&R"},
    {"id": 3781, "name": "Federal Way P&R (320th)"},
    {"id": 3782, "name": "Auburn P&R"},
    {"id": 3783, "name": "Star Lake P&R"},
    {"id": 3784, "name": "Holy Spirit Lutheran Church"},
    {"id": 3785, "name": "Kent/Des Moines P&R"},
    {"id": 3786, "name": "Kent/James St. P&R"},
    {"id": 3787, "name": "Burien Transit Center"},
    {"id": 3788, "name": "Tukwila"},
    {"id": 3789, "name": "Maple Valley P&R"},
    {"id": 3790, "name": "South Renton P&R"},
    {"id": 3791, "name": "Renton Highlands P&R (St. Matts)"},
    {"id": 3792, "name": "Issaquah Transit Center"},
    {"id": 3793, "name": "Mercer Island P&R"},
    {"id": 3794, "name": "Mercer Island Presbyterian"},
    {"id": 3795, "name": "Newport Hills P&R"},
    {"id": 3796, "name": "Newport Hills Community Church"},
    {"id": 3797, "name": "Newport Covenant Church"},
    {"id": 3798, "name": "South Bellevue P&R"},
    {"id": 3799, "name": "Wilburton"},
    {"id": 3800, "name": "Eastgate P&R"},
    {"id": 3801, "name": "North Bend P&R"},
    {"id": 3802, "name": "Evergreen Point P&R"},
    {"id": 3803, "name": "Grace Lutheran Church"},
    {"id": 3804, "name": "South Kirkland P&R"},
    {"id": 3805, "name": "Overlake P&R"},
    {"id": 3806, "name": "Houghton P&R"},
    {"id": 3807, "name": "Bethel Lutheran"},
    {"id": 3808, "name": "Redmond P&R"},
    {"id": 3809, "name": "Saint Thomas Episcopal"},
    {"id": 3810, "name": "Valley Center"},
    {"id": 3811, "name": "Bear Creek P&R"},
    {"id": 3812, "name": "Kingsgate P&R"},
    {"id": 3813, "name": "Brickyard P&R"},
    {"id": 3814, "name": "Northshore P&R"},
    {"id": 3815, "name": "Kenmore P&R"},
    {"id": 3816, "name": "Bethany Bible Church"},
    {"id": 3817, "name": "Bothell P&R"},
    {"id": 3818, "name": "Woodinville P&R"},
    {"id": 3819, "name": "Olson & Meyers"},
    {"id": 3820, "name": "Spokane Street P&R"},
    {"id": 3821, "name": "Greenlake P&R"},
    {"id": 3822, "name": "Northgate TC"},
    {"id": 3823, "name": "North Jackson Park"},
    {"id": 3824, "name": "Shoreline"},
    {"id": 3825, "name": "112th St. & I-5"},
    {"id": 3826, "name": "Ober Park"},
    {"id": 3827, "name": "Vashon Heights"},
    {"id": 3828, "name": "Mountlake Terrace P&R"},
    {"id": 3829, "name": "Bethesda Lutheran"},
    {"id": 3830, "name": "Edmonds Station"},
    {"id": 3831, "name": "Edmonds P&R"},
    {"id": 3832, "name": "Lynnwood P&R"},
    {"id": 3833, "name": "Swamp Creek P&R"},
    {"id": 3834, "name": "Mariner P&R"},
    {"id": 3835, "name": "Snohomish"},
    {"id": 3836, "name": "Marysville - Ash Ave"},
    {"id": 3837, "name": "116th & I-5 - Marysville"},
    {"id": 3838, "name": "SR-531 - Marysville"},
    {"id": 3839, "name": "Arlington P&R"},
    {"id": 3840, "name": "Stanwood"},
    {"id": 3841, "name": "Monroe"},
    {"id": 3842, "name": "Federal Way"},
    {"id": 3843, "name": "Port Orchard Armory"},
    {"id": 3844, "name": "Southworth Ferry P&R"},
    {"id": 3845, "name": "McWilliams P&R"},
    {"id": 3846, "name": "Bethany Lutheran Church"},
    {"id": 3847, "name": "Gateway Fellowship"},
    {"id": 3848, "name": "Agate Pass P&R/Clearwater"},
    {"id": 3849, "name": "Kingston Ferry P&R"},
    {"id": 3850, "name": "Suquamish United Church of Christ"},
    {"id": 3851, "name": "Bainbridge Island Ferry"},
    {"id": 3852, "name": "Puyallup Station (NB)"},
    {"id": 3853, "name": "72nd Street Transit Center"},
    {"id": 3855, "name": "DuPont"},
    {"id": 3856, "name": "Aurora Village TC"},
    {"id": 3857, "name": "Aurora Nazarene"},
    {"id": 3858, "name": "Saint Margaret's Episcopal"},
    {"id": 3861, "name": "Lake Meridian P&R"},
    {"id": 3862, "name": "Smokey Pt. Church"},
    {"id": 3863, "name": "Eastmont P&R"},
    {"id": 3864, "name": "McCollum Park P&R"},
    {"id": 3865, "name": "Canyon Park P&R"},
    {"id": 3866, "name": "Korean Presby. P&R"},
    {"id": 3867, "name": "Georges Kountry Korner"},
    {"id": 3868, "name": "Poulsbo Church of the Nazarene"},
    {"id": 3870, "name": "Harper Evangelical Free Church"},
    {"id": 3871, "name": "Mullenix Road"},
    {"id": 3873, "name": "TCC P&R"},
    {"id": 3874, "name": "Ash Way P&R"},
    {"id": 3875, "name": "Bonney Lake P&R"},
    {"id": 3876, "name": "Tukwila Int. Station"},
    {"id": 3877, "name": "South Hill P&R"},
    {"id": 3878, "name": "South Tacoma East - 1"},
    {"id": 3879, "name": "Issaquah Highlands"},
    {"id": 3880, "name": "Lake Stevens TC"},
    {"id": 3881, "name": "Liberty Bay Presbyterian"},
    {"id": 3882, "name": "NK Baptist"},
    {"id": 3883, "name": "Preston P&R"},
    {"id": 3884, "name": "Bayside Community Church"},
    {"id": 3885, "name": "Ollala Valley Fire Station"},
    {"id": 3886, "name": "Bremerton Ferry"},
    {"id": 3888, "name": "Puyallup Fair's Red Lot"},
    {"id": 3889, "name": "Marysville - Cedar & Grove"},
    {"id": 3890, "name": "Stanwood II"},
    {"id": 3891, "name": "Marysville I P&R"},
    {"id": 3892, "name": "Martha Lake Covenant Church"},
    {"id": 3893, "name": "South Sammammish P&R"},
    {"id": 3894, "name": "Renton City Municipal Garage"},
    {"id": 3895, "name": "Tibbetts Lot"},
    {"id": 3896, "name": "Renton Transit Center"},
    {"id": 3897, "name": "Calvary Christian Assembly"},
    {"id": 3898, "name": "Maple Valley Town Square"},
    {"id": 3899, "name": "All Saints Lutheran Church"},
    {"id": 3900, "name": "City View Church"},
    {"id": 3901, "name": "Northwest University 6710 Bldg."},
    {"id": 3902, "name": "Sammamish Lutheran P&R"},
    {"id": 3903, "name": "Redmond Ridge P&R"},
    {"id": 3904, "name": "Kennydale United Methodist Church"},
    {"id": 3905, "name": "Nativity Lutheran Church"},
    {"id": 3906, "name": "South Jackson P&R"},
    {"id": 3907, "name": "South SeaTac (LR)"},
    {"id": 3908, "name": "Everett Station"},
    {"id": 3909, "name": "Bremerton (SR-303/Riddell Road)"},
    {"id": 3910, "name": "Silverdale"},
    {"id": 3911, "name": "Tukwila Station (CR)"},
    {"id": 3913, "name": "Sumner Station Garage"},
    {"id": 3914, "name": "Tacoma Dome"},
    {"id": 3915, "name": "Bothell (SR-527/185th Street)"},
    {"id": 3916, "name": "SR-3/SR-303"},
    {"id": 3917, "name": "SR-16/SR-160"},
    {"id": 3918, "name": "I-5 & 175th"}
]

In [41]:
pnr_capacity = pd.read_csv(os.path.join(valid_config['model_dir'], 'inputs/scenario/networks/p_r_nodes.csv'))
df = pnr_capacity.merge(pnr_boardings, left_on='ZoneID', right_on='otaz')
df.rename(columns={'ZoneID': 'taz', 'trexpfac': 'Model Boardings'}, inplace=True)
df['Boardings/Capacity'] = df['Model Boardings']/df['Capacity']
# df.head()

In [42]:
df_station_names = pd.DataFrame(stations)
df = df.merge(df_station_names, how='left', left_on='taz', right_on='id')

In [43]:
df['color'] = np.where(df['Boardings/Capacity'] > 1, 'Boardings/Capacity > 1', 'Boardings/Capacity <= 1')

fig = px.scatter(df, y='Model Boardings', x='Capacity', title='Model Boardings vs Capacity',
                 hover_data={'name': True, 'Model Boardings': True, 'Capacity': True, 'Boardings/Capacity': ':.2f'},
                 color='color')
fig.update_layout(height=600, width=800)
fig.show()

In [44]:
gdf = gpd.GeoDataFrame(df, geometry=gpd.points_from_xy(df.XCoord, df.YCoord), crs='EPSG:2285')
gdf.to_crs('EPSG:4326', inplace=True)

fig = px.scatter_mapbox(gdf, lat=gdf.geometry.y, lon=gdf.geometry.x, color='Boardings/Capacity', 
                        size='Boardings/Capacity', hover_data=['name','taz','Model Boardings', 'Capacity'], 
                        title='Park and Ride Usage vs Capacity', zoom=8)
fig.update_layout(mapbox_style="carto-positron")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

fig.show()

C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\3247811068.py:4: DeprecationWarning:

*scatter_mapbox* is deprecated! Use *scatter_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [45]:
# # get observed data
p_r_observe_data = pd.read_sql(text("SELECT * FROM observed_park_and_ride"), con=conn.connect())
# filter to latest data record for each park and ride (only 2021 and later years)
idx = p_r_observe_data.groupby(['lot_name'])['data_year'].transform(max) == p_r_observe_data['data_year']
df_p_r_observe_data = p_r_observe_data[idx].copy()
df_p_r_observe_data = df_p_r_observe_data.loc[df_p_r_observe_data['data_year']>=2021].copy()

# add station names to node file
df_p_r_nodes = pnr_capacity.merge(pd.DataFrame(stations), left_on="ZoneID", right_on="id")

# transform to geodataframe
gdf_p_r_nodes = gpd.GeoDataFrame(
    df_p_r_nodes, geometry=gpd.points_from_xy(df_p_r_nodes.XCoord, df_p_r_nodes.YCoord), crs="EPSG:2285"
)

gdf_p_r_observe_data = gpd.GeoDataFrame(
    df_p_r_observe_data, geometry=gpd.points_from_xy(df_p_r_observe_data.x_coord, df_p_r_observe_data.y_coord), crs="EPSG:2285"
)

# merge with park and ride name
gdf_p_r_data_name = gdf_p_r_nodes.merge(gdf_p_r_observe_data[['data_year', 'lot_name', 'lot_address', 'city','capacity', 'occupancy']],
                                        left_on="name",right_on="lot_name")

# merge by nearest location
gdf_p_r_data_near = gpd.sjoin_nearest(gdf_p_r_nodes.loc[~(gdf_p_r_nodes["name"].isin(gdf_p_r_data_name.name))],
                                      gdf_p_r_observe_data[['data_year', 'lot_name', 'lot_address', 'city','capacity', 'occupancy', 'geometry']],
                                      max_distance=500)

df_col = ['NodeID', 'ZoneID', 'data_year', 'name', 
          'lot_name', 'lot_address', 'city', 'Capacity', 'capacity', 'occupancy', 
          'XCoord', 'YCoord', 'geometry']
gdf_p_r_data = pd.concat([gdf_p_r_data_name[df_col],gdf_p_r_data_near[df_col]]).copy()

# merge boardings
gdf_p_r_data = gdf_p_r_data.merge(pnr_boardings, left_on="ZoneID", right_on="otaz")

gdf_p_r_data = gdf_p_r_data[['NodeID', 'ZoneID', 'data_year', 'name', 'lot_name', 'lot_address',
       'city', 'Capacity', 'capacity', 'occupancy', 'trexpfac', 'XCoord', 'YCoord',
       'geometry']].copy().rename(columns={'trexpfac':'boardings'})

gdf_p_r_data['boardings - occupancy'] = gdf_p_r_data['boardings'] - gdf_p_r_data['occupancy']
gdf_p_r_data['percent diff'] = gdf_p_r_data['boardings - occupancy'] / gdf_p_r_data['occupancy']

gdf_p_r_data.to_crs('EPSG:4326', inplace=True)


C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\2556493080.py:4: FutureWarning:

The provided callable <built-in function max> is currently using SeriesGroupBy.max. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string "max" instead.



In [46]:
fig = px.scatter_mapbox(gdf_p_r_data, lat=gdf_p_r_data.geometry.y, lon=gdf_p_r_data.geometry.x, color='percent diff', 
                        hover_data=['name','ZoneID','boardings', 'Capacity', 'boardings - occupancy'], 
                        title='Park and Ride Usage vs Observed Data', zoom=8)
fig.update_layout(mapbox_style="carto-positron")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})

fig.show()

C:\Users\modeller\AppData\Local\Temp\ipykernel_68480\960525819.py:1: DeprecationWarning:

*scatter_mapbox* is deprecated! Use *scatter_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



In [47]:
gdf_p_r_data[['ZoneID', 'data_year', 'name','city', 'capacity', 'occupancy', 'boardings', 'boardings - occupancy', 'percent diff']].sort_values(['city','name'])

ZoneID  data_year                        name           city  capacity  \
34     3839       2023               Arlington P&R      Arlington        25   
106    3862       2023           Smokey Pt. Church      Arlington        50   
49     3899       2023  All Saints Lutheran Church         Auburn        75   
9      3782       2023                  Auburn P&R         Auburn       244   
59     3758       2023         Auburn Station (CR)         Auburn       520   
..      ...        ...                         ...            ...       ...   
75     3788       2023                     Tukwila        Tukwila       267   
115    3876       2023        Tukwila Int. Station        Tukwila       600   
54     3751       2023        Tukwila Station (CR)        Tukwila       390   
30     3826       2023                   Ober Park  Vashon Island        48   
29     3818       2023             Woodinville P&R    Woodinville       438   

     occupancy  boardings  boardings - occupancy  percent diff  
34           5         11                      6             1  
106         13         21                      8             1  
49          20         64                     44             2  
9           53          7                    -46            -1  
59         295        426                    131             0  
..         ...        ...                    ...           ...  
75         206         21                   -185            -1  
115        570        530                    -40            -0  
54         133         48                    -85            -1  
30           7          4                     -3            -0  
29          39         31                     -8            -0  

[129 rows x 9 columns]

# Transit Submodes by Purpose
Model Outputs Only (insufficient samples available from survey)

In [48]:
import h5py
myh5 = h5py.File(r'..\..\..\..\inputs\scenario\landuse\hh_and_persons.h5', 'r')
person = pd.read_csv(r'..\..\..\..\outputs\daysim\_person.tsv', sep='\t')

In [49]:
# Create a DataFrame from the h5 file
df_person = pd.DataFrame()
for col in ['hhno','pno','prace']:
    df_person[col] = myh5['Person'][col][:]

df_trip = df_trip.merge(df_person[['hhno','pno','prace']], on=['hhno','pno'], how='left')

In [50]:
# Create group of work, school, and all other purposes
df_trip['Purpose Type'] = 'Other'
df_trip.loc[df_trip['dpurp']==0, 'Purpose Type'] = 'Home'
df_trip.loc[df_trip['dpurp']==1, 'Purpose Type'] = 'Work'
df_trip.loc[df_trip['dpurp']==2, 'Purpose Type'] = 'School'

# Rename path types
df_trip.loc[df_trip['pathtype']==1, 'Path Type'] = 'Drive'
df_trip.loc[df_trip['pathtype']==3, 'Path Type'] = 'Bus'
df_trip.loc[df_trip['pathtype']==4, 'Path Type'] = 'Light Rail'
df_trip.loc[df_trip['pathtype']==5, 'Path Type'] = 'Ferry 1'
df_trip.loc[df_trip['pathtype']==6, 'Path Type'] = 'Commuter Rail'
df_trip.loc[df_trip['pathtype']==7, 'Path Type'] = 'Ferry 2'

df = pd.pivot_table(df_trip[(df_trip['dpurp']!=0) & (df_trip['pathtype']!=0)], values='trexpfac', index='Path Type', columns='Purpose Type', aggfunc="sum")

df['Total'] = df.sum(axis=1)
for row in df.index:
    for col in ['Work','School','Other']:
        df.loc[row, col + ' %'] = df.loc[row, col] / df.loc[row, 'Total']

df[['Work %','School %','Other %']] = df[['Work %','School %','Other %']].map("{:,.1%}".format)
df[['Work %','School %','Other %']]

Purpose Type  Work % School % Other %
Path Type                            
Bus            14.4%    13.0%   72.6%
Commuter Rail  47.9%     2.2%   49.9%
Drive          20.5%     5.4%   74.1%
Ferry 1        54.5%     8.5%   37.0%
Ferry 2        57.7%     6.4%   35.9%
Light Rail     30.5%    11.8%   57.6%

#### Transit Submodes by Person Race

In [51]:

race_dict = {
    '1': 'White alone',
    '2': 'Black or African American alone',
    '3': 'American Indian alone',
    '4': 'Alaska Native alone',
    '5': 'American Indian and Alaska Native tribes specified',
    '6': 'Asian alone',
    '7': 'Native Hawaiian and Other Pacific Islander alone',
    '8': 'Some Other Race alone',
    '9': 'Two or More Races'
}


df_trip['Race'] = df_trip['prace'].astype('int').astype('str').map(race_dict)

In [52]:
# Submode Ridership by race
df = pd.pivot_table(df_trip[(df_trip['pathtype']!=0)], values='trexpfac', index='Path Type', columns='Race', aggfunc="sum")
race_cols = ['White alone','Black or African American alone','American Indian alone',
             'Alaska Native alone','American Indian and Alaska Native tribes specified','Asian alone',
             'Native Hawaiian and Other Pacific Islander alone','Some Other Race alone','Two or More Races']
# Calculate shares of total by Race for each Path Type
df['Total'] = df.sum(axis=1).astype('float')
for row in df.index:
    for col in race_cols:
        df[col] = df[col].astype('float')
        df.loc[row, col] = df.loc[row, col].astype('float') / df.loc[row, 'Total'].astype('float')
df[race_cols] = df[race_cols].map("{:,.1%}".format)

In [53]:
df[race_cols]

Race          White alone Black or African American alone  \
Path Type                                                   
Bus                 63.1%                            6.6%   
Commuter Rail       65.2%                            6.5%   
Drive               65.1%                            5.7%   
Ferry 1             71.8%                            4.5%   
Ferry 2             72.5%                            3.8%   
Light Rail          62.2%                            6.2%   

Race          American Indian alone Alaska Native alone  \
Path Type                                                 
Bus                            0.6%                0.1%   
Commuter Rail                  0.8%                0.1%   
Drive                          0.6%                0.1%   
Ferry 1                        0.6%                0.1%   
Ferry 2                        0.5%                0.1%   
Light Rail                     0.5%                0.1%   

Race          American Indian and Alaska Native tribes specified Asian alone  \
Path Type                                                                      
Bus                                                         0.1%       15.8%   
Commuter Rail                                               0.0%       11.9%   
Drive                                                       0.1%       14.3%   
Ferry 1                                                     0.1%       10.5%   
Ferry 2                                                     0.1%       11.4%   
Light Rail                                                  0.1%       17.5%   

Race          Native Hawaiian and Other Pacific Islander alone  \
Path Type                                                        
Bus                                                       0.8%   
Commuter Rail                                             1.4%   
Drive                                                     1.0%   
Ferry 1                                                   0.7%   
Ferry 2                                                   0.7%   
Light Rail                                                0.8%   

Race          Some Other Race alone Two or More Races  
Path Type                                              
Bus                            4.0%              8.9%  
Commuter Rail                  5.3%              8.7%  
Drive                          4.2%              8.9%  
Ferry 1                        2.9%              8.8%  
Ferry 2                        3.1%              7.9%  
Light Rail                     4.0%              8.6%